# QA-QC of Kriging results

In [ ]:
import geolime as geo
import numpy as np
from pyproj import CRS
import pyvista as pv

pv.set_jupyter_backend('html')
geo.Project().set_crs(CRS("EPSG:20350"))

In [ ]:
dh = geo.read_file("../data/domained_drillholes.geo")

In [ ]:
domain_solid = geo.datasets.load("rocklea_dome/domain_mesh.dxf")
domain_solid.name = "channel_hg"

In [ ]:
bm = geo.read_file("../data/block_model_panel.geo")

In [ ]:
domain_solid.contains(dh)

In [ ]:
dh.set_region("channel_hg", "in_channel_hg & Fe_pct.notna()")

In [ ]:
geo.histogram_plot(data=[{"object":bm, "property":"Fe_kriged"}],nbins=20)

In [ ]:
geo.plot_2d(bm, "Fe_kriged", "mean")

In [ ]:
dh_pv = dh.to_pyvista('Fe_pct', "channel_hg")
bm_pv = bm.to_pyvista('Fe_kriged', "channel_hg")

In [ ]:
p = pv.Plotter()

p.add_mesh(dh_pv.tube(radius=10))
p.add_mesh_threshold(bm_pv,show_edges=True, opacity=0.7)
p.set_scale(zscale=20)
p.remove_scalar_bar("Fe_pct")

p.show()

In [ ]:
slices = bm_pv.slice_orthogonal(x=547.8e3, y=7.4760e6, z=430)
p = pv.Plotter()
p.add_mesh(dh_pv.tube(radius=10))
p.add_mesh(slices,show_edges=True, opacity=1)
p.set_scale(zscale=20)
p.remove_scalar_bar("Fe_pct")

p.show()

In [ ]:
bm["density"] = 4

In [ ]:
geo.swath_plot(bm, "Fe_kriged", "channel_hg", 50, "Y", "blue")

In [ ]:
geo.swath_plot(bm, "Fe_kriged", "channel_hg", 50, "Y", "blue", density="density", proportion="in_channel_prop")

In [ ]:
geo.swath_plot(
    [
        {"obj":bm, "attribute":"Fe_kriged", "region":"channel_hg", "swath_interval":50, "axis":"Y", "color": "blue", "density": "density", "proportion": "in_channel_prop"},
        {"obj":dh, "attribute":"Fe_pct", "region":"channel_hg", "swath_interval":50, "axis":"Y_M", "color": "red"}
    ]
)

In [ ]:
grades = np.linspace(30, 60, 30)

In [ ]:
bm.keep_only_cells('channel_hg')

In [ ]:
fig = geo.gtc(bm, 'Fe_kriged', 'density', grades, proportion="in_channel_prop")
fig.update_layout(
    {
        "xaxis":{"range":[28, 60]},
         "yaxis2":{"range":[45, 60]}
    }
)
fig.update_layout(yaxis_title="Tonnage", xaxis_title="Cutoff grade", yaxis2_title="Mean Grade", title = "Grade-Tonnage curve")